In [1]:
import plotly
plotly.offline.init_notebook_mode()
import plotly.graph_objs as go
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from plotly.tools import FigureFactory as FF
import plotly.tools as tls  
import pandas as pd
import numpy as np
from scipy import stats
import matplotlib.pyplot as plt
import pprint
pp = pprint.PrettyPrinter(indent=4)
from itertools import combinations 

# compare runs

In [ ]:
# links = ["/mnt/aertslab/USERS/Ahmed/0_FINAL_SEGMENTAION_DATA/harvard-rt/0_competition_scores/tune_tc_scores.csv",
#          "/output/103_focal-tversky-loss-0.0005/103_focal-tversky-loss-0.0005.csv",
#         "/mnt/aertslab/USERS/Ahmed/0_FINAL_SEGMENTAION_DATA/harvard-rt/12_label_interpolated_pr/92_tversky-loss-0.001_103_focal-tversky-loss-0.0005/103_focal-tversky-loss-0.0005.csv",
#         "/mnt/aertslab/USERS/Ahmed/0_FINAL_SEGMENTAION_DATA/harvard-rt/12_label_interpolated_pr/95_bce-dice-loss-0.001_103_focal-tversky-loss-0.0005/103_focal-tversky-loss-0.0005.csv"]

#    "/output/105_focal-tversky-loss-vary-lr/105_focal-tversky-loss-vary-lr.csv",
#         "/output/106_focal-tversky-loss-vary-lr-tight/106_focal-tversky-loss-vary-lr-tight.csv",
#         "/output/107_focal-tversky-loss-vary-lr-tight-2/107_focal-tversky-loss-vary-lr-tight-2.csv",
#        "/output/108_focal-tversky-loss-vary-lr-tight-2-affine/108_focal-tversky-loss-vary-lr-tight-2-affine.csv",
    
    
    
# links = [

#     "/output/103_focal-tversky-loss-0.0005/103_focal-tversky-loss-0.0005.csv",
#     "/output/109_focal-tversky-loss-0.0005-augment/single_prediction/109_focal-tversky-loss-0.0005-augment.csv",
#     "/output/109_focal-tversky-loss-0.0005-augment/multi_prediction/109_focal-tversky-loss-0.0005-augment.csv",
#     "/output/110_focal-tversky-loss-0.0005-augment-rt/single_prediction/110_focal-tversky-loss-0.0005-augment-rt.csv",
#     "/output/110_focal-tversky-loss-0.0005-augment-rt/multi_prediction/110_focal-tversky-loss-0.0005-augment-rt.csv",
#     "/output/111_focal-tversky-loss-0.0005-augment-maastro/111_focal-tversky-loss-0.0005-augment-maastro.csv",
#     "/output/112_focal-tversky-loss-0.0005-augment-rt-maastro/112_focal-tversky-loss-0.0005-augment-rt-maastro.csv"
# ]


# distance metrics in mm
# metrics = ["average_surface_distance_gt_to_pr", "average_surface_distance_pr_to_gt",
#            "x_distance", "y_distance", "z_distance", "distance", "robust_hausdorff"]
# 0 to 1 fraction metrics
# metrics = ["precision", "recall", "dice", "jaccard", "surface_dice", "segmentation_score",
#            "overlap_fraction_gt_with_pr", "overlap_fraction_pr_with_gt"]


# metrics = ["x_distance", "y_distance", "z_distance", "distance"]
# metrics = ["dice"] # , "surface_dice" , "jaccard", "segmentation_score"

# load becnhmark and reindex to match others

In [ ]:
tune_benchmark = pd.read_csv("/mnt/aertslab/USERS/Ahmed/0_FINAL_SEGMENTAION_DATA/harvard-rt/0_competition_scores/tune_tc_scores.csv")
ref = df = pd.read_csv("/output/109_focal-tversky-loss-0.0005-augment/multi_prediction/109_focal-tversky-loss-0.0005-augment.csv")
tune_benchmark = tune_benchmark.set_index('patient_id')
tune_benchmark = tune_benchmark.reindex(index=ref['patient_id'])
tune_benchmark = tune_benchmark.reset_index()

# statistics functions

In [32]:
def get_stats(a,b):
    """
    preforms "greater-than" test
    H0 = no difference
    HA = a is greater than b or the opposite based on the sign of the test.
    
    # https://stackoverflow.com/questions/15984221/how-to-perform-two-sample-one-tailed-t-test-with-numpy-scipy
    It goes on to say that scipy always gives the test statistic as signed. This means that given p and t values
    from a two-tailed test, you would reject the null hypothesis of a greater-than test when p/2 < alpha and t > 0, 
    and of a less-than test when p/2 < alpha and t < 0.
    # https://medium.com/@kangeugine/hypothesis-test-21795f788f7d
    # https://www.datascienceblog.net/post/statistical_test/signed_wilcox_rank_test/
    # http://pytolearn.csd.auth.gr/d1-hyptest/12/ttest-paired.html
    
    # 95% CI
    # https://scientificallysound.org/2017/05/16/independent-t-test-python/
    
    # parametric vs non-parametric
    # https://help.xlstat.com/s/article/what-is-the-difference-between-a-parametric-and-a-nonparametric-test?language=en_US
    # https://help.xlstat.com/s/article/which-statistical-test-should-you-use?language=en_US
    
    # astresk
    https://www.graphpad.com/support/faq/what-is-the-meaning-of--or--or--in-reports-of-statistical-significance-from-prism-or-instat/
    
    """
    return {
        "t_test_two_sided": stats.ttest_ind(a, b),
        "wilcoxon_two_sided": stats.wilcoxon(a, b, alternative="two-sided"),
        "wilcoxon_greater": stats.wilcoxon(a, b, alternative="greater"),
        "t_test_rel_two_sided": stats.ttest_rel(a, b)
    }

def interpret_stats(result):
    alpha = 0.05
    test = "t_test_rel_two_sided"
    p = result[test][1]/2

    if (p < alpha):
        if (result[test][0] > 0):
            # print ("p-value :: {}, reject null hypothesis, mean of a is greater than mean of b".format(p))
            a = "better  ----  "
            b = "  ----  worse"
        else:
            # print ("p-value :: {}, reject null hypothesis, mean of b is greater than mean of a".format(p))
            a = "worse  ----  "
            b = "  ----  better"
#     else:
#         print ("p-value :: {}, accept null hypothesis (means are equal)".format(p))
    
    if p > alpha:
        return "ns"
    elif p <= alpha and p > 0.01:
        text = "*"
    elif p <= 0.01 and p > 0.001:
        text = "**"
    elif p <= 0.001 and p > 0.0001:
        text = "***"
    else: # p <= 0.0001
        text = "****"
    return "{}{}{}".format(a, text, b)

# set params for dfs

In [50]:
metric = "dice"

raw_links = [
    {"title": "top_coder_ref",
     "name": "top_coder_ref",
     "subfolder": "",
      metric: tune_benchmark[metric].tolist()},
    {"title": "103_some_aug",
     "name": "103_focal-tversky-loss-0.0005",
     "subfolder": ""},
    {"title": "109_all_aug_single",
     "name": "109_focal-tversky-loss-0.0005-augment",
     "subfolder": "single_prediction"},
#     {"title": "109_all_aug_multi",
#      "name": "109_focal-tversky-loss-0.0005-augment",
#      "subfolder": "multi_prediction"},
#     {"title": "110_rt_only_single",
#      "name": "110_focal-tversky-loss-0.0005-augment-rt",
#      "subfolder": "single_prediction"},
#     {"title": "110_rt_only_multi",
#      "name": "110_focal-tversky-loss-0.0005-augment-rt",
#      "subfolder": "multi_prediction"},
#     {"title": "111_maastro_only",
#      "name": "111_focal-tversky-loss-0.0005-augment-maastro",
#      "subfolder": ""},
    {"title": "112_maastro_rt",
     "name": "112_focal-tversky-loss-0.0005-augment-rt-maastro",
     "subfolder": ""},
]

# load dfs and calculate statistics

In [51]:
for obj in raw_links[1:]:
    if obj["subfolder"] == "":
        obj["link"] = "/output/{}/{}.csv".format(obj["name"], obj["name"])
    else: 
        obj["link"] = "/output/{}/{}/{}.csv".format(obj["name"], obj["subfolder"], obj["name"])   
    
    # get df
    df = pd.read_csv(obj["link"], index_col=0)
    obj[metric] = df[metric].tolist()

p_values = []
# figure out p values
combos = list(combinations(raw_links, 2))
for combo in combos:
    result = get_stats(combo[0][metric], combo[1][metric])
    p_values.append({"from": combo[0]["title"], 
                     "to": combo[1]["title"],
                     "p": interpret_stats(result)})


# print (raw_links[0])

# box plot

In [52]:
title = "plot"
data = []
for obj in raw_links:
    trace = go.Box(
        y=obj[metric],
        boxpoints='all',
        name=obj["title"],
        jitter=0.3,
        notched=False,
        pointpos=0,
        whiskerwidth=0.2,
        marker=dict(
            size=2,
        ),
        line=dict(width=1),
    )
    data.append(trace)
    
height = 1.1
dip = 0.02
for p in p_values:
    trace = go.Scatter(x=[p["from"], p["from"], p["to"], p["to"]], 
                       y=[height-dip, height, height, height-dip], 
                       mode="lines",
                       showlegend=False,
                       line=dict(color='black', width=1))
    data.append(trace)
    trace = go.Scatter(x=[p["from"]], 
                       y=[height], 
                       mode="text",
                       text = p["p"],
                       showlegend=False,
                       textposition="top right")
    data.append(trace)
    height += 0.1
    

layout = go.Layout(
   title=title,
    yaxis=dict(
        autorange=False,
        title="",
        range=[0,height+0.1],
        showgrid=True,
        zeroline=True,
#         dtick=0.1,
#         gridcolor='rgb(255, 255, 255)',
        gridwidth=1,
#         zerolinecolor='rgb(255, 255, 255)',
        zerolinewidth=2,
    ),
#     paper_bgcolor='rgb(243, 243, 243)',
#     plot_bgcolor='rgb(243, 243, 243)',
    showlegend=True,
#     boxmode='group'
)
fig = go.Figure(data=data, layout=layout)
iplot(fig, filename=title, image="svg") # svg

# STATISTICS

{   't_test_rel_two_sided': Ttest_relResult(statistic=1.7948784117685492, pvalue=0.07585328005462287),
    't_test_two_sided': Ttest_indResult(statistic=0.6641191971835111, pvalue=0.5074191443751825),
    'wilcoxon_greater': WilcoxonResult(statistic=3008.0, pvalue=0.0017258281452838104),
    'wilcoxon_two_sided': WilcoxonResult(statistic=1457.0, pvalue=0.0034516562905676207)}


p-value :: 0.037926640027311435, reject null hypothesis, mean of a is greater than mean of b


In [ ]:
results = stats.ttest_rel(data['FSIQ'], data['PIQ']) 
alpha = 0.05
if (results[0] > 0) & (results[1]/2 < alpha):
    print "reject null hypothesis, mean of {} is greater than mean of {}".format('FSIQ','PIQ')
else:
    print "accept null hypothesis"
    
# one-tailed, less than 'FSIQ
results = stats.ttest_rel(data['PIQ'], data['FSIQ']) 
alpha = 0.05
if (results[0] < 0) & (results[1]/2 < alpha):
    print "reject null hypothesis, mean of {} is less than mean of {}".format('PIQ','FSIQ')
else:
    print "accept null hypothesis"

In [43]:
 stats.ttest_rel(pd.read_csv(links[1])["dice"], pd.read_csv(links[3])["dice"]) 

Ttest_relResult(statistic=1.957153167382927, pvalue=0.05326473687174525)

# BAR PLOT

In [14]:
title = "7 models - test set n={}".format(n_test_samples)
data = []
metric = "dice"
for idx, link in enumerate(links):
    df = pd.read_csv(link, index_col=0)
    name = "{} n={}".format(link.split("/")[2], df.shape[0])
    values = df[metric].tolist()
    trace = go.Histogram(
        x=values,
        opacity=1,
        name=name
    )
    data.append(trace)
    
layout = go.Layout(
      yaxis=dict(
            title="",
      ),
          xaxis=dict(
            title="dice",
      )
  )
    
fig = go.Figure(data=data, layout=layout)
iplot(fig, filename=title, image="")

## temporary analysis for dice

In [27]:
for link in links[1:]:
    counter = 0
    df = pd.read_csv(link, index_col=0)
    name = "{} n={}".format(link.split("/")[2], df.shape[0])
    for i in range(len(df)):
        if df["x_distance"][i] == 0 and df["dice"][i] == 0 and df["distance"][i] == 0:
            counter+=1
    print (name, counter)

101_dice-loss-0.0005 n=96 2
102_tversky-loss-0.0005 n=96 2
103_focal-tversky-loss-0.0005 n=96 2
100_bce-dice-loss-0.0005 n=96 7
104_wce-dice-loss-0.0005 n=96 5


## temporary analysis for distances

In [78]:
for link in links:
    df = pd.read_csv(link, index_col=0)
    name = "{} n={}".format(link.split("/")[2], df.shape[0])
    # check within respective limits
    within_limit = 0
    for i in range(len(df)):
        if df["x_distance"][i] < 50 and df["y_distance"][i] < 50 and df["z_distance"][i] < 66:
            within_limit += 1
    print (name, round(within_limit/len(df),2), round(within_limit/96,2) , round(len(df)/96, 2)) 
        
    


90_precision-loss-0.001 n=11 1.0 0.11 0.11
91_dice-loss-0.001 n=72 0.89 0.67 0.75
92_tversky-loss-0.001 n=84 0.85 0.74 0.88
93_focal-tversky-loss-0.001 n=85 0.79 0.7 0.89
94_bce-loss-0.001 n=62 0.85 0.55 0.65
95_bce-dice-loss-0.001 n=75 0.91 0.71 0.78
96_wce-dice-loss-0.001 n=79 0.84 0.69 0.82


In [69]:
len(df)

79

# HEATMAP MATRIX

In [48]:
z = []
x = metrics
y = []
for link in links:
    df = pd.read_csv(link, index_col=0)
    name = link.split("/")[2]
    y.append(name)
    matrix = []
    for metric in metrics:
        matrix.append(np.mean(df[metric]))
    z.append(matrix)

trace = go.Heatmap(z=z,
                   x=metrics,
                   y=y,
                   colorscale = 'Bluered')
data=[trace]
iplot(data, filename='labelled-heatmap')

# PLOT TRAINING PROGRESS

In [48]:
runs = [103, 107, 108, 109, 110, 111, 112] # 90, 91, 92, 93, 94, 95
names = ["focal-tversky-loss-0.0005", "focal-tversky-loss-vary-lr-tight-2",
         "focal-tversky-loss-vary-lr-tight-2-affine", "focal-tversky-loss-0.0005-augment",
        "focal-tversky-loss-0.0005-augment-rt", "focal-tversky-loss-0.0005-augment-maastro",
        "focal-tversky-loss-0.0005-augment-rt-maastro"] # "precision-loss-0.001", "dice-loss-0.001", "tversky-loss-0.001", "focal-tversky-loss-0.001", "bce-loss-0.001", "bce-dice-loss-0.001"
show_train_loss = True
show_val_loss = True
show_lr  = False

In [49]:
traces = []

# loss
for run, name in zip(runs, names):
    loss = np.load("/output/{}_{}/{}_loss.npy".format(run, name, run))
    val_loss = np.load("/output/{}_{}/{}_val_loss.npy".format(run, name, run))
    batches_per_epoch = int(len(loss)/len(val_loss))
    print (len(loss), len(val_loss), batches_per_epoch, val_loss.min())
    if show_train_loss:
        traces.append(go.Scatter(
            x=[i for i in range(len(loss))],
            y=loss,
            mode='lines',
            name='train loss run #{} {}'.format(run, name),
            line=dict(width=1)
        ))
    if show_val_loss:
        traces.append(go.Scatter(
            x=[0] + [x for x in range(batches_per_epoch-1, len(loss), batches_per_epoch)],
            y=[0] + val_loss.tolist(),
            mode='lines',
            name='val loss run #{} {}'.format(run, name),
            line=dict(width=1)
        ))
        
    if show_lr:
        lr = np.load("/output/{}_{}/{}_lr.npy".format(run, name, run))
        traces.append(go.Scatter(
            x=[0] + [x for x in range(batches_per_epoch-1, len(loss), batches_per_epoch)],
            y=[0] + [x*1000 for x in lr.tolist()],
            mode='lines',
            name='lr run #{} {}'.format(run, name),
            line=dict(width=1)
        ))

layout = go.Layout(
    title='runs',
    showlegend=True
)

fig = go.Figure(data=traces, layout=layout)
iplot(fig,  ) # image="svg"

2700 150 18 0.2992176016171773
2700 150 18 0.294783095518748
5400 300 18 0.28758646647135416
7200 400 18 0.27741834918657937
1800 300 6 0.376037061214447
3300 300 11 0.27939602732658386
1800 300 6 0.3512290120124817


In [8]:
len(lr)

64

In [13]:
lr

array([1.00000005e-03, 1.00000005e-03, 1.00000005e-03, 1.00000005e-03,
       1.00000005e-03, 1.00000005e-03, 1.00000005e-03, 1.00000005e-03,
       1.00000005e-03, 1.00000005e-03, 1.00000005e-03, 1.00000005e-03,
       1.00000005e-03, 1.00000005e-03, 2.00000009e-04, 2.00000009e-04,
       2.00000009e-04, 2.00000009e-04, 2.00000009e-04, 2.00000009e-04,
       2.00000009e-04, 2.00000009e-04, 2.00000009e-04, 2.00000009e-04,
       2.00000009e-04, 2.00000009e-04, 2.00000009e-04, 2.00000009e-04,
       2.00000009e-04, 2.00000009e-04, 2.00000009e-04, 2.00000009e-04,
       2.00000009e-04, 4.00000026e-05, 4.00000026e-05, 4.00000026e-05,
       4.00000026e-05, 4.00000026e-05, 4.00000026e-05, 8.00000089e-06,
       8.00000089e-06, 1.60000013e-06, 1.60000013e-06, 3.20000026e-07,
       3.20000026e-07, 6.40000053e-08, 6.40000053e-08, 1.28000011e-08,
       1.28000011e-08, 2.56000021e-09, 2.56000021e-09, 5.12000053e-10,
       5.12000053e-10, 1.02400012e-10, 1.02400012e-10, 2.04800031e-11,
      

# TRASH

In [14]:
# x_data = ['37-dice', '38-tversky', '39-tversky-focal', '40-tversky-focal-inverse']
x_data = ["x_distance", "y_distance", "z_distance", "dice"]

# y_data = [df[x] for x in x_data]
y_data = [df1[col] for col in x_data]

colors = ['rgba(93, 164, 214, 0.5)', 
          'rgba(255, 144, 14, 0.5)', 
          'rgba(44, 160, 101, 0.5)', 
          'rgba(255, 65, 54, 0.5)']

traces = []

for xd, yd, cls in zip(x_data, y_data, colors):
        traces.append(go.Box(
            y=yd,
            name=xd,
            boxpoints='all',
            jitter=0.3,
            notched=False,
            pointpos=0,
            whiskerwidth=0.2,
            fillcolor=cls,
            marker=dict(
                size=2,
            ),
            line=dict(width=1),
        ))

layout = go.Layout(
    title=name,
    yaxis=dict(
        autorange=False,
        range=[0,180],
        showgrid=True,
        zeroline=True,
#         dtick=0.1,
        gridcolor='rgb(255, 255, 255)',
        gridwidth=1,
        zerolinecolor='rgb(255, 255, 255)',
        zerolinewidth=2,
    ),
    margin=dict(
        l=40,
        r=30,
        b=80,
        t=100,
    ),
    paper_bgcolor='rgb(243, 243, 243)',
    plot_bgcolor='rgb(243, 243, 243)',
    showlegend=False
)

fig = go.Figure(data=traces, layout=layout)
iplot(fig, filename=name, image='svg' )

In [ ]:
/home/hosny/testmount/aertslab/DATA

In [33]:
# x_data = ['37-dice', '38-tversky', '39-tversky-focal', '40-tversky-focal-inverse']
x_data = ["x_distance", "y_distance", "z_distance", "distance"]

# y_data = [df[x] for x in x_data]
y_data = [df1[col] for col in x_data]

colors = ['rgba(93, 164, 214, 0.5)', 
          'rgba(255, 144, 14, 0.5)', 
          'rgba(44, 160, 101, 0.5)', 
          'rgba(255, 65, 54, 0.5)']

traces = []

for xd, yd, cls in zip(x_data, y_data, colors):
        traces.append(go.Box(
            y=yd,
            name=xd,
            boxpoints='all',
            jitter=0.3,
            notched=False,
            pointpos=0,
            whiskerwidth=0.2,
            fillcolor=cls,
            marker=dict(
                size=2,
            ),
            line=dict(width=1),
        ))

layout = go.Layout(
    title='run #55 n=52',
    yaxis=dict(
        autorange=True,
        showgrid=True,
        zeroline=True,
#         dtick=0.1,
        gridcolor='rgb(255, 255, 255)',
        gridwidth=1,
        zerolinecolor='rgb(255, 255, 255)',
        zerolinewidth=2,
    ),
    margin=dict(
        l=40,
        r=30,
        b=80,
        t=100,
    ),
    paper_bgcolor='rgb(243, 243, 243)',
    plot_bgcolor='rgb(243, 243, 243)',
    showlegend=False
)

fig = go.Figure(data=traces, layout=layout)
iplot(fig, filename="plotly-fig", image='svg' )